In [3]:
df.columns

Index(['id', 'NAME', 'host id', 'host name', 'neighbourhood group',
       'neighbourhood', 'lat', 'long', 'country', 'country code',
       'instant_bookable', 'cancellation_policy', 'room type',
       'Construction year', 'price', 'service fee', 'minimum nights',
       'number of reviews', 'last review', 'reviews per month',
       'review rate number', 'calculated host listings count',
       'availability 365', 'house_rules', 'license'],
      dtype='object')

In [71]:
import pandas as pd
import random

df = pd.read_csv('Airbnb_Open_Data.csv')
df = df.drop('host_identity_verified', axis=1)
df['description'] = df['NAME']
df['price'] = df['price'].dropna().apply(lambda x : int(x[1:].strip().replace(',', '')))
df['sq. meters'] = df['price'].apply(lambda x : random.choices([25, 40, 45, 55, 60, 70], weights=[5, 5, 4, 3, 2, 1])[0])
df = df[['price', 'sq. meters', 'description', 'neighbourhood group', 'host name', 'cancellation_policy', 'house_rules']]
df = df[df['house_rules']!='#NAME?'].dropna().reset_index(drop=True)
df = df[0:10000]

C:\Users\ardit\AppData\Local\Temp\ipykernel_25752\2207992772.py:4: DtypeWarning: Columns (25) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('Airbnb_Open_Data.csv')


In [72]:
import pandas as pd
from tqdm import tqdm
from sentence_transformers import SentenceTransformer
tqdm.pandas()

model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

#encode df version: for small dataset only
df['text_vector_'] = df['description'].progress_apply(lambda x : model.encode(x).tolist())
df

100%|██████████| 10000/10000 [17:37<00:00,  9.45it/s]


price  sq. meters                                       description  \
0      966.0          25                Clean & quiet apt home by the park   
1      142.0          25                             Skylit Midtown Castle   
2      620.0          45               THE VILLAGE OF HARLEM....NEW YORK !   
3      204.0          55  Entire Apt: Spacious Studio/Loft by central park   
4      577.0          25         Large Cozy 1 BR Apartment In Midtown East   
...      ...         ...                                               ...   
9995   745.0          60   Upper West Side 1BR next to subway/Central Park   
9996  1135.0          45      Modern and Bright Studio Apt in Williamsburg   
9997    59.0          45               Holiday in Trendy Williamsburg Apt!   
9998  1055.0          25             Greenwich Village| Private Queen room   
9999   285.0          25               Comfortable bedroom in spacious apt   

     neighbourhood group host name cancellation_policy  \
0               Brooklyn  Madaline              strict   
1              Manhattan     Jenna            moderate   
2              Manhattan     Elise            flexible   
3              Manhattan    Lyndon            moderate   
4              Manhattan  Michelle            flexible   
...                  ...       ...                 ...   
9995           Manhattan    Doreen              strict   
9996            Brooklyn   Shannon              strict   
9997            Brooklyn     Peter              strict   
9998           Manhattan     Kelly            flexible   
9999            Brooklyn    Arthur              strict   

                                            house_rules  \
0     Clean up and treat the home the way you'd like...   
1     Pet friendly but please confirm with me if the...   
2     I encourage you to use my kitchen, cooking and...   
3     Please no smoking in the house, porch or on th...   
4                     No smoking, please, and no drugs.   
...                                                 ...   
9995  Our Herbivorian House manual with detailed rul...   
9996                                 No smoking please!   
9997  We suggest you use email or texting contact us...   
9998  Please treat this house as if it is your own. ...   
9999  Please, No smoking and no pets. We do require ...   

                                           text_vector_  
0     [-0.047521110624074936, 0.03044620156288147, 0...  
1     [-0.04690079391002655, 0.061329323798418045, 0...  
2     [0.00039011164335533977, 0.018310122191905975,...  
3     [-0.04602213576436043, 0.015605293214321136, 0...  
4     [-0.04859349876642227, -0.01263828668743372, 0...  
...                                                 ...  
9995  [-0.0346745029091835, -0.005859952419996262, 0...  
9996  [-0.016586357727646828, 0.020517650991678238, ...  
9997  [-0.05095353722572327, 0.08510775864124298, -0...  
9998  [0.00017118529649451375, 0.010939894244074821,...  
9999  [-0.01795135624706745, -0.029596544802188873, ...  

[10000 rows x 8 columns]

In [ ]:
df = pd.read_parquet('df_encoded.parquet')
df['neighbourhood group'][0:2500] = df['neighbourhood group'][0:2500].apply(lambda x : 'Manhattan')
df['neighbourhood group'][2500:5000] = df['neighbourhood group'][0:2500].apply(lambda x : 'Brooklyn')
df['neighbourhood group'][5000:7500] = df['neighbourhood group'][0:2500].apply(lambda x : 'Queens')
df['neighbourhood group'][7500:] = df['neighbourhood group'][0:2500].apply(lambda x : 'Bronx')
df['location'] = df['neighbourhood group']
df = df[['price', 'sq. meters', 'description', 'location', 'host name', 'cancellation_policy', 'house_rules', 'text_vector_']]
df = df.reset_index(drop=True)
df

In [145]:
from sklearn.neighbors import NearestNeighbors
import numpy as np
import pandas as pd

from sentence_transformers import SentenceTransformer

# df = df.read_parquet('df_encoded.parquet')
model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

#prepare model
# nbrs = NearestNeighbors(n_neighbors=3, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())

In [ ]:
import gradio as gr
import statistics

def closest_number(x):
    closest_numbers = [10, 20, 30, 40]
    closest_number = closest_numbers[0]
    min_distance = abs(x - closest_number)
    for number in closest_numbers[1:]:
        distance = abs(x - number)
        if distance < min_distance:
            closest_number = number
            min_distance = distance
    return closest_number

def search(df, query):
    product = model.encode(query).tolist()
    # product = df.iloc[0]['text_vector_'] #use one of the products as sample

    nbrs = NearestNeighbors(n_neighbors=3, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())
    distances, indices = nbrs.kneighbors([product]) #input the vector of the reference object

    #print out the description of every recommended product
    df_search = df.iloc[list(indices)[0]].drop(['text_vector_'], axis=1) #.sort_values('avgFeedbackScore', ascending=False)

    return df_search.sort_values('price', ascending=False)

def filter_df(df, column_name, filter_type, filter_value):
    if filter_type == '==':
        df_filtered = df[df[column_name]==filter_value]
    elif filter_type == '>=':
        df_filtered = df[df[column_name]>=filter_value]
    elif filter_type == '<=':
        df_filtered = df[df[column_name]<=filter_value]
    return df_filtered

history = list()
def predict(input1, input2, input3, input4):
    history.append([input1, input2, input3, input4])

    print(history)
    df_location = filter_df(df, 'location', '==', input3)
    df_size = filter_df(df_location, 'sq. meters', '==', input2)
    df_price = filter_df(df_size, 'price', '<=', input1)
    df_result = search(df_price, input4)

    prediction = [
        round(statistics.mean([x[0] for x in history])), #price
        closest_number(statistics.mean([x[1] for x in history])), #square room
        statistics.mode([x[2] for x in history]) #state
    ]

    return df_result, prediction

with gr.Blocks(theme=gr.themes.Soft(primary_hue='amber', secondary_hue='gray', neutral_hue='amber')) as demo:
    gr.Markdown(
    """
    # Airbnb Search Engine
    """
    )
    input1 = gr.Slider(100, 1200, value=700, step_size=100, label="Max Price")
    input2 = gr.Radio([25, 40, 45, 55, 60, 70], multiselect=False, label='square meters', value=45)
    input3 = gr.Radio(['Manhattan', 'Brooklyn', 'Queens', 'Bronx'], multiselect=False, label='State', value='Queens')
    input4 = gr.Textbox(label='Query', value='I want to take a break from work 😴!!!')

    btn = gr.Button(value="Search for a Room")
    output1 = gr.Dataframe()
    output2 = gr.Textbox(label='prediction for the next search')
    # btn.click(greet, inputs='text', outputs=['dataframe'])
    btn.click(predict, [input1, input2, input3, input4], [output1, output2])
demo.launch(share=False)

In [ ]:
import os
os.system('pip install openpyxl')
os.system('pip install sentence-transformers')
import pandas as pd
import gradio as gr
import statistics
from sklearn.neighbors import NearestNeighbors
from sentence_transformers import SentenceTransformer

df = pd.read_parquet('df_encoded.parquet')
df['neighbourhood group'][0:2500] = df['neighbourhood group'][0:2500].apply(lambda x : 'Manhattan')
df['neighbourhood group'][2500:5000] = df['neighbourhood group'][0:2500].apply(lambda x : 'Brooklyn')
df['neighbourhood group'][5000:7500] = df['neighbourhood group'][0:2500].apply(lambda x : 'Queens')
df['neighbourhood group'][7500:] = df['neighbourhood group'][0:2500].apply(lambda x : 'Bronx')
df['location'] = df['neighbourhood group']
df = df[['price', 'sq. meters', 'description', 'location', 'host name', 'cancellation_policy', 'house_rules', 'text_vector_']]
df = df.reset_index(drop=True)
df

model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

#prepare model #we run it anew in the search function every time, after the initial filtering
# nbrs = NearestNeighbors(n_neighbors=3, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())

def closest_number(x):
    closest_numbers = [25, 40, 45, 55, 60, 70]
    closest_number = closest_numbers[0]
    min_distance = abs(x - closest_number)
    for number in closest_numbers[1:]:
        distance = abs(x - number)
        if distance < min_distance:
            closest_number = number
            min_distance = distance
    return closest_number

def search(df, query):
    product = model.encode(query).tolist()
    # product = df.iloc[0]['text_vector_'] #use one of the products as sample

    nbrs = NearestNeighbors(n_neighbors=3, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())
    distances, indices = nbrs.kneighbors([product]) #input the vector of the reference object

    #print out the description of every recommended product
    df_search = df.iloc[list(indices)[0]].drop(['text_vector_'], axis=1) #.sort_values('avgFeedbackScore', ascending=False)

    return df_search.sort_values('price', ascending=False)

def filter_df(df, column_name, filter_type, filter_value):
    if filter_type == '==':
        df_filtered = df[df[column_name]==filter_value]
    elif filter_type == '>=':
        df_filtered = df[df[column_name]>=filter_value]
    elif filter_type == '<=':
        df_filtered = df[df[column_name]<=filter_value]
    return df_filtered

In [7]:
def predict(history, input1, input2, input3, input4):
    history.append([input1, input2, input3, input4])

    print(history)
    df_location = filter_df(df, 'location', '==', input3)
    df_size = filter_df(df_location, 'sq. meters', '==', input2)
    df_price = filter_df(df_size, 'price', '<=', input1)
    df_result = search(df_price, input4)

    prediction = [
        round(statistics.mean([x[0] for x in history])), #price
        closest_number(statistics.mean([x[1] for x in history])), #square meters
        statistics.mode([x[2] for x in history]) #state
    ]

    print(history)

    return df_result, prediction

In [8]:
with gr.Blocks(theme=gr.themes.Soft(primary_hue='amber', secondary_hue='gray', neutral_hue='amber')) as demo:
    history = gr.Variable(value=[]) #beginning
    gr.Markdown(
    """
    # Airbnb Search Engine
    """
    )
    input1 = gr.Slider(100, 1200, value=700, step_size=100, label="Max Price")
    input2 = gr.Radio([25, 40, 45, 55, 60, 70], multiselect=False, label='square meters', value=45)
    input3 = gr.Radio(['Manhattan', 'Brooklyn', 'Queens', 'Bronx'], multiselect=False, label='State', value='Brooklyn')
    input4 = gr.Textbox(label='Query', value='I want to take a break from work 😴!!!')

    btn = gr.Button(value="Search for a Room")
    output1 = gr.Dataframe()
    output2 = gr.Textbox(label='prediction for the next search')
    # btn.click(greet, inputs='text', outputs=['dataframe'])
    btn.click(predict, [history, input1, input2, input3, input4], [output1, output2])
demo.launch(share=False)

c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\gradio\deprecation.py:43: UserWarning: You have unused kwarg parameters in Slider, please remove them: {'step_size': 100}
  warnings.warn(
c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\gradio\deprecation.py:43: UserWarning: You have unused kwarg parameters in Radio, please remove them: {'multiselect': False}
  warnings.warn(


Running on local URL:  http://127.0.0.1:7863

To create a public link, set `share=True` in `launch()`.


[[700, 45, 'Brooklyn', 'I want to take a break from work 😴!!!']]
[[700, 45, 'Brooklyn', 'I want to take a break from work 😴!!!']]
[[700, 45, 'Brooklyn', 'I want to take a break from work 😴!!!'], [700, 45, 'Brooklyn', 'I want to take a break from work 😴!!!']]
[[700, 45, 'Brooklyn', 'I want to take a break from work 😴!!!'], [700, 45, 'Brooklyn', 'I want to take a break from work 😴!!!']]
